In [1]:
from datasets import load_dataset

dataset = load_dataset("mnist")

Extracting data files:   0%|          | 0/4 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/60000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/10000 [00:00<?, ? examples/s]

Dataset mnist downloaded and prepared to /root/.cache/huggingface/datasets/mnist/mnist/1.0.0/fda16c03c4ecfb13f165ba7e29cf38129ce035011519968cdaf74894ce91c9d4. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [2]:
import numpy as np
from PIL import Image
import io
import tensorflow as tf

def convert_image(byte_like_str_image):
    return tf.convert_to_tensor(np.asarray(Image.open(io.BytesIO(byte_like_str_image['bytes']))), dtype = tf.float32)

In [3]:
from keras.utils import to_categorical

dataset_train = dataset['train'].to_pandas()
dataset_train['image'] = dataset_train['image'].map(convert_image)

dataset_test = dataset['test'].to_pandas()
dataset_test['image'] = dataset_test['image'].map(convert_image)

# Convert labels to NumPy arrays
X_train = np.array(dataset_train['image'].tolist())
y_train = np.array(dataset_train['label'])

X_test = np.array(dataset_test['image'].tolist())
y_test = np.array(dataset_test['label'])
# dataset_train['label'] = dataset_train['label'].astype('float32')
# dataset_test['label'] = dataset_test['label'].astype('float32')



In [4]:
import tensorflow as tf

model = tf.keras.models.Sequential([
  tf.keras.layers.Flatten(input_shape=(28, 28)),
  tf.keras.layers.Dense(128, activation='relu'),
  tf.keras.layers.Dense(10)
])

In [5]:
model.compile(
    optimizer=tf.keras.optimizers.Adam(0.001),
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=[tf.keras.metrics.SparseCategoricalAccuracy()],
)

In [6]:
# model.fit(
#     dataset_train['image'], dataset_test['label'],
#     epochs=10,
#     validation_data=(dataset_test['image'], dataset_test['label']),
# )
# dataset_train['label'].head(50)
model.fit(X_train, y_train, epochs=5, validation_data=(X_test, y_test))

dataset_train.info()



Epoch 1/5
1875/1875 [==============================] - 7s 3ms/step - loss: 2.6159 - sparse_categorical_accuracy: 0.8597 - val_loss: 0.5951 - val_sparse_categorical_accuracy: 0.8762
Epoch 2/5
1875/1875 [==============================] - 6s 3ms/step - loss: 0.4041 - sparse_categorical_accuracy: 0.9071 - val_loss: 0.4567 - val_sparse_categorical_accuracy: 0.9024
Epoch 3/5
1875/1875 [==============================] - 6s 3ms/step - loss: 0.2977 - sparse_categorical_accuracy: 0.9247 - val_loss: 0.3300 - val_sparse_categorical_accuracy: 0.9237
Epoch 4/5
1875/1875 [==============================] - 5s 3ms/step - loss: 0.2646 - sparse_categorical_accuracy: 0.9344 - val_loss: 0.2909 - val_sparse_categorical_accuracy: 0.9368
Epoch 5/5
1875/1875 [==============================] - 5s 3ms/step - loss: 0.2418 - sparse_categorical_accuracy: 0.9391 - val_loss: 0.2886 - val_sparse_categorical_accuracy: 0.9330
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 60000 entries, 0 to 59999
Data columns (total

In [8]:
loss, accuracy = model.evaluate(X_test, y_test)
accuracy

313/313 [==============================] - 1s 3ms/step - loss: 0.2886 - sparse_categorical_accuracy: 0.9330


0.9330000281333923